In [1]:
import pandas as pd
import datetime as dt
import requests
from pprint import pprint
from bs4 import BeautifulSoup, Tag
import numpy as np
import time
import plotly.graph_objects as go
import re
import os

In [ ]:
with open('D:\\lianz\\Desktop\\Python\\personal_projects\\finance_dashboard\\alpha_vantage_api.txt','r') as f:
    alpha_vantage_api = f.readlines()[0]

In [ ]:
#TODO: perform analysis in Jupyter notebook - decide on information to query
#TODO: choose information to store in RDBMS
#TODO: define schema in RDBMS
#TODO: build airflow pipeline to extract, transform and load into RDBMS
#TODO: build dash (dash over streamlit for adaptability)
#TODO: deploy dash
#TODO: have highlighted areas in basketball court that shows top 10 players in every range of shooting based on FG%

># Request for Traditional Endpoint Data

In [ ]:
url = "https://stats.nba.com/stats/leaguedashplayerstats?" # /leaguedashplayerstats?, /playerestimatedmetrics?, /leaguedashplayerclutch?, /leagueleaders? /playergamelogs?, /leaguedashplayershotlocations?

parameters = {
'College': '', 
'Conference': '', # East, West
'Country': '',
'DateFrom': '',
'DateTo': '',
'DistanceRange': '', # (Only for leaguedashplayershotlocations) 5ft Range, 8ft Range, By Zone
'Division': '', # Central, Atlantic, Southeast, Southwest, Northwest, Pacific 
'DraftPick': '', # 1st Round, 2nd Round, 1st Pick, Lottery Pick, Top 5 Pick, Top 10 Pick, Top 15 Pick, Top 20 Pick, Top 25 Pick, Picks 11 Thru 20, Picks 21 Thru 30, Undrafted
'DraftYear': '',
'GameScope': '',
'GameSegment': '', # First Half, Second Half, Overtime
'Height': '', # LT 6-0, GT 6-9
'LastNGames': '0',
'LeagueID': '00',
'Location': '', # Home, Road
'MeasureType': 'Base', # Base, Advanced, Misc, Scoring, Usage, Opponent, Defense, 
'Month': '0', # January=4, February=5, ..., September=9, October=1, November=2, December=3
'OpponentTeamID': '0',
'Outcome': '', # W, L
'PORound': '0', #Conference Quarter-Finals=1, Conference Semi-Finals=2, Conference Finals=3, Finals=4
'PaceAdjust': 'N',
'PerMode': 'Totals', #Per Mode: Totals, PerGame, Per100Possessions, Per100Plays, Per48, Per40, Per36, PerMinute, PerPossession, PerPlay, MinutesPer
'Period': '0', #Quarter: 1,2,3,4,5,6,7,8,9,10
'PlayerExperience': '', # Rookie, Sophomore, Veteran
'PlayerPosition': '', # Center=C, Forward=F, Guard=G
'PlusMinus': 'N',
'Rank': 'N',
'Season': '2022-23', # YYYY-YY, All Time for leagueleaders endpoint
'SeasonSegment': '', # Pre All-Star, Post All-Star
'SeasonType': 'Regular Season', # Season Type: Regular Season, Playoffs, Pre Season, All Star, PlayIn
'StatCategory': '', # (Only for leagueleaders endpoint) PTS, MIN, FGA, FGM, TOV, FG_PCT, FG3_PCT, FG3A, FG3M, FTM, FTA, FT_PCT, OREB, DREB, REB, AST, BLK, STL, 
'ShotClockRange': '', # 24-22, 22-18 Very Early, 18-15 Very Early, 15-7 Average, 7-4 Late, 4-0 Very Late
'StarterBench': '', # Starters, Bench
'TeamID': '0',
'VsConference': '', # East, West
'VsDivision': '', # Central, Atlantic, Southeast, Southwest, Northwest, Pacific 
'Weight': '', # GT 200, LT 200, 
'AheadBehind': '', # (Only for clutch endpoint) Ahead or Behind, Behind or Tied, Ahead or Tied
'ActiveFlag': '', # (Only for leagueleaders endpoint) No, Yes
'ClutchTime': '', # (Only for clutch endpoint) Last 5 mins, Last 4 mins, Last 3 mins, Last 2 mins, Last 1 mins, Last 30 Seconds, Last 10 Seconds 
'PointDiff': '', # (Only for clutch endpoint) 5, 4, 3, 2, 1
}

headers = {
'Accept': '*/*',
'Accept-Encoding': 'gzip, deflate, br',
'Accept-Language': 'en-US,en;q=0.9',
'Connection': 'keep-alive',
'Host': 'stats.nba.com',
'Origin': 'https://www.nba.com',
'Referer': 'https://www.nba.com/',
'sec-ch-ua': '"Chromium";v="112", "Google Chrome";v="112", "Not:A-Brand";v="99"',
'sec-ch-ua-mobile': '?0',
'sec-ch-ua-platform': "Windows",
'Sec-Fetch-Dest': 'empty',
'Sec-Fetch-Mode': 'cors',
'Sec-Fetch-Site': 'same-site',
'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/112.0.0.0 Safari/537.36',
}

r = requests.request('GET', url=url, headers=headers, params=parameters)

In [ ]:
r = r.json()

In [ ]:
r['resultSets'][0]['headers']

In [ ]:
n_group = 3
to_be_grouped = r['resultSets']['headers'][1]['columnNames'][6:]
grouped = []

for i in range(0, len(to_be_grouped), n_group):
    mini_groups = to_be_grouped[i:i+n_group]
    grouped.append(mini_groups)

grouped

In [ ]:
shotDistance = r['resultSets']['headers'][0]['columnNames']
stats_category = grouped[0]

In [ ]:
new_column_index = [shotDistance, stats_category]
index = pd.MultiIndex.from_product(new_column_index, names=['shotDistance','category'])

In [ ]:
index = [
    ("", 'PLAYER_ID'),
    ("", 'PLAYER_NAME'),
    ("", 'TEAM_ID'),
    ("", 'TEAM_ABBREVIATION'),
    ("", 'AGE'),
    ("", 'NICKNAME'),
    ('Less Than 5 ft.',    'FGM'),
    ('Less Than 5 ft.',    'FGA'),
    ('Less Than 5 ft.', 'FG_PCT'),
    (        '5-9 ft.',    'FGM'),
    (        '5-9 ft.',    'FGA'),
    (        '5-9 ft.', 'FG_PCT'),
    (      '10-14 ft.',    'FGM'),
    (      '10-14 ft.',    'FGA'),
    (      '10-14 ft.', 'FG_PCT'),
    (      '15-19 ft.',    'FGM'),
    (      '15-19 ft.',    'FGA'),
    (      '15-19 ft.', 'FG_PCT'),
    (      '20-24 ft.',    'FGM'),
    (      '20-24 ft.',    'FGA'),
    (      '20-24 ft.', 'FG_PCT'),
    (      '25-29 ft.',    'FGM'),
    (      '25-29 ft.',    'FGA'),
    (      '25-29 ft.', 'FG_PCT'),
    (      '30-34 ft.',    'FGM'),
    (      '30-34 ft.',    'FGA'),
    (      '30-34 ft.', 'FG_PCT'),
    (      '35-39 ft.',    'FGM'),
    (      '35-39 ft.',    'FGA'),
    (      '35-39 ft.', 'FG_PCT'),
    (        '40+ ft.',    'FGM'),
    (        '40+ ft.',    'FGA'),
    (        '40+ ft.', 'FG_PCT')
]

In [ ]:
df = pd.DataFrame.from_records(r['resultSets']['rowSet'], columns=pd.MultiIndex.from_tuples(index))
df

In [ ]:
for i in df.columns.to_flat_index():
    print(" ".join(i).strip())

# Scrape

### Define years to scrape

In [ ]:
start_year = 1996
end_year = 2022
years = []

while start_year <= end_year:
    years.append(f'{start_year}-{str(start_year+1)[-2:]}')
    start_year += 1

### Time between requests

In [ ]:
lag = np.random.randint(low=5, high=25)

### Function for Scraping

In [ ]:
def scrape_nba(year, **kwargs):
    url = "https://stats.nba.com/stats/leaguedashplayershotlocations?" # /leaguedashplayerstats?, /playerestimatedmetrics?, /leaguedashplayerclutch?, /leagueleaders? /playergamelogs?, /leaguedashplayershotlocations?
    
    parameters = {
    # 'AheadBehind': '', # (Only for clutch endpoint) Ahead or Behind, Behind or Tied, Ahead or Tied
    # 'ActiveFlag': '', # (Only for leagueleaders endpoint) No, Yes
    # 'ClutchTime': '', # (Only for clutch endpoint) Last 5 mins, Last 4 mins, Last 3 mins, Last 2 mins, Last 1 mins, Last 30 Seconds, Last 10 Seconds 
    'College': '', 
    'Conference': '', # East, West
    'Country': '',
    'DateFrom': '',
    'DateTo': '',
    'DistanceRange': '5ft Range', # (Only for leaguedashplayershotlocations) 5ft Range, 8ft Range, By Zone
    'Division': '', # Central, Atlantic, Southeast, Southwest, Northwest, Pacific 
    'DraftPick': '', # 1st Round, 2nd Round, 1st Pick, Lottery Pick, Top 5 Pick, Top 10 Pick, Top 15 Pick, Top 20 Pick, Top 25 Pick, Picks 11 Thru 20, Picks 21 Thru 30, Undrafted
    'DraftYear': '',
    'GameScope': '',
    'GameSegment': '', # First Half, Second Half, Overtime
    'Height': '', # LT 6-0, GT 6-9
    'LastNGames': '0',
    'LeagueID': '00',
    'Location': '', # Home, Road
    'MeasureType': 'Base', # Base, Advanced, Misc, Scoring, Usage, Opponent, Defense, 
    'Month': '0', # January=4, February=5, ..., September=9, October=1, November=2, December=3
    'OpponentTeamID': '0',
    'Outcome': '', # W, L
    'PORound': '0', #Conference Quarter-Finals=1, Conference Semi-Finals=2, Conference Finals=3, Finals=4
    'PaceAdjust': 'N',
    'PerMode': 'Totals', #Per Mode: Totals, PerGame, Per100Possessions, Per100Plays, Per48, Per40, Per36, PerMinute, PerPossession, PerPlay, MinutesPer
    'Period': '0', #Quarter: 1,2,3,4,5,6,7,8,9,10
    'PlayerExperience': '', # Rookie, Sophomore, Veteran
    'PlayerPosition': '', # Center=C, Forward=F, Guard=G
    'PlusMinus': 'N',
    # 'PointDiff': '', # (Only for clutch endpoint) 5, 4, 3, 2, 1
    'Rank': 'N',
    'Season': year, # YYYY-YY, All Time for leagueleaders endpoint
    'SeasonSegment': '', # Pre All-Star, Post All-Star
    'SeasonType': 'Regular Season', # Season Type: Regular Season, Playoffs, Pre Season, All Star, PlayIn
    'StatCategory': '', # (Only for leagueleaders endpoint) PTS, MIN, FGA, FGM, TOV, FG_PCT, FG3_PCT, FG3A, FG3M, FTM, FTA, FT_PCT, OREB, DREB, REB, AST, BLK, STL, 
    'ShotClockRange': '', # 24-22, 22-18 Very Early, 18-15 Very Early, 15-7 Average, 7-4 Late, 4-0 Very Late
    'StarterBench': '', # Starters, Bench
    'TeamID': '0',
    'VsConference': '', # East, West
    'VsDivision': '', # Central, Atlantic, Southeast, Southwest, Northwest, Pacific 
    'Weight': '', # GT 200, LT 200, 
    }

    headers = {
    'Accept': '*/*',
    'Accept-Encoding': 'gzip, deflate, br',
    'Accept-Language': 'en-US,en;q=0.9',
    'Connection': 'keep-alive',
    'Host': 'stats.nba.com',
    'Origin': 'https://www.nba.com',
    'Referer': 'https://www.nba.com/',
    'sec-ch-ua': '"Chromium";v="112", "Google Chrome";v="112", "Not:A-Brand";v="99"',
    'sec-ch-ua-mobile': '?0',
    'sec-ch-ua-platform': "Windows",
    'Sec-Fetch-Dest': 'empty',
    'Sec-Fetch-Mode': 'cors',
    'Sec-Fetch-Site': 'same-site',
    'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/112.0.0.0 Safari/537.36',
    }

    r = requests.request('GET', url=url, headers=headers, params=parameters)
    r = r.json()
    return r

In [ ]:
def process_scraped_data(result, index):
    df = pd.DataFrame.from_records(result['resultSets']['rowSet'], columns=pd.MultiIndex.from_tuples(index))
    return df

### Scrape

In [ ]:
combined_df = []
begin_time = time.time()
lag_time = 0
for year in years:
    r = scrape_nba(year)
    df = process_scraped_data(result=r, index=index)
    df['year'] = year
    combined_df.append(df)
    print(f'Successfully retrieved data for Season {year}')
    lag = np.random.randint(low=5, high=25)
    lag_time += lag
    print(f'Delaying for: {lag}s\nCurrent total lag time: {lag_time}s')
    time.sleep(lag)
time_taken = time.time() - begin_time
print(f'Total time taken: {round(time_taken/60, 2)}mins')

In [ ]:
final_df = pd.concat(combined_df, axis=0)

In [ ]:
final_df.to_csv('player_shotLocations.csv', index=False)

In [ ]:
player_ID = final_df[[("", 'PLAYER_ID'),("", 'PLAYER_NAME'), ("", 'NICKNAME')]].drop_duplicates(subset=("", 'PLAYER_ID'))
team_ID = final_df[[("", 'TEAM_ID'),("","TEAM_ABBREVIATION")]].drop_duplicates()

In [ ]:
print(f'''
Number of players from 1996-2023: {len(player_ID)}
Number of teams from 1996-2023: {len(team_ID)}
''')

In [ ]:
from nba_api import NBA

In [ ]:
len([
            {"text": name, "stretch": False} for name in [" ".join(i).strip()
                                                          for i in index]
        ])

In [ ]:
pd.read_csv('player_shotLocations.csv', header=1, index_col=0)

In [ ]:
[tuple(row) for row in df.itertuples()]

# Scrape from Basketball Reference

## Game shots Scraping

In [3]:
def request_soup_for_game(year: str, month: str, day: str, team: str):
    url = f'https://www.basketball-reference.com/boxscores/shot-chart/{year}{month}{day}0{team}.html'
    page = requests.get(url=url)
    soup = BeautifulSoup(page.content, "html.parser")
    if soup.find('h1').text == 'Page Not Found (404 error)':
        return False
    else:
        return soup


def get_shot_area(soup):
    shot_area = soup.find_all("div", class_="shot-area")
    return shot_area


def get_game_meta(soup):
    game_meta = soup.find_all("div", class_='scorebox_meta')[0].text
    return game_meta


def get_customdata(df: pd.DataFrame) -> list:
    customdata = []
    for row in df.itertuples(index=False):
        customdata.append(tuple(row))
    return customdata

def create_df(shot_area, game_meta):
    df = dict(player_name=[], time_left=[], team_name=[], score_status=[],
              x_shot_pos=[], y_shot_pos=[], quarter=[], shot_status=[], full_text=[])
    for elem in shot_area:
        for content in elem.contents:
            if isinstance(content, Tag) and not re.search(r'alt="nbahalfcourt"', str(content)):
                shot_pos = re.findall(
                    r'\d+(?=px)', str(content.attrs.get('style')))
                tooltip = content.attrs.get('tip')
                status = content.attrs.get('class')
                df['x_shot_pos'].append(int(shot_pos[1]))
                df['y_shot_pos'].append(470 - int(shot_pos[0]))
                df['quarter'].append(tooltip.split(',')[0])
                df['time_left'].append(re.findall(
                    r'(?!\s)(\d+:\d+.\d)(?= remaining)', tooltip)[0])
                df['shot_status'].append(status[-1])
                df['player_name'].append(re.findall(
                    r"(?=<br>)(.*)((?= missed)|(?= made))", tooltip)[0][0][4:])
                df['team_name'].append(re.findall(
                    r"(?=ft<br>)(.*)((?= tied)|(?= now trails)|(?= trails)|(?= leads))", tooltip)[0][0][6:].replace('now', ''))
                df['score_status'].append(re.findall(
                    r"(?=ft<br>).*", tooltip)[0][6:])
                df['full_text'].append(tooltip)

    df = pd.DataFrame.from_dict(df,).astype({'quarter': 'category',
                                            'shot_status': 'category', })
    df['datetime'] = dt.datetime.strptime(re.findall(
        r'\d+:\d+ \w+, \w+ \d+, \d+', game_meta)[0], "%I:%M %p, %B %d, %Y")
    # location = re.findall(
    #     r'(?=\d{4})(\w+\s\w+,.+,\s.+)(?=\nLogos)', game_meta)[0][4:].split(',')
    # # arena = location[0].strip()
    # city = location[1].strip()
    # state = location[2].strip()

    # df['arena'] = arena
    # df['city'] = city
    # df['state'] = state

    return df

In [4]:
team_abbs = {
"Atlanta Hawks": 'ATL',
"Brooklyn Nets": 'BKN',
"Boston Celtics": 'BOS',
"Charlotte Hornets": 'CHH',
"Chicago Bulls": 'CHI',
"Cleveland Cavaliers": 'CLE',
"Dallas Mavericks": 'DAL',
"Denver Nuggets": 'DEN',
"Detroit Pistons": 'DET',
"Golden State Warriors": 'GSW',
"Houston Rockets": 'HOU',
"Indiana Pacers": 'IND',
"Los Angeles Clippers": 'LAC',
"Los Angeles Lakers": 'LAL',
"Memphis Grizzlies": 'MEM',
"Miami Heat": 'MIA',
"Milwaukee Bucks": 'MIL',
"Minnesota Timberwolves": 'MIN',
"New Orleans Pelicans": 'NOP',
"New York Knicks": 'NYK',
"Oklahoma City Thunder": 'OKC',
"Orlando Magic": 'ORL',
"Philadelphia 76ers": 'PHI',
"Phoenix Suns": 'PHX',
"Portland Trail Blazers": 'POR',
"Sacramento Kings": 'SAC',
"San Antonio Spurs": 'SAS',
"Toronto Raptors": 'TOR',
"Utah Jazz": 'UTA',
"Washington Wizards": 'WAS',
'Seattle SuperSonics': 'SEA',
'Vancouver Grizzlies': 'VAN',
'New Jersey Nets': 'NJN',
'New Orleans Hornets': 'NOH',
'Charlotte Bobcats': 'CAB',
'New Orleans/Oklahoma City Hornets': 'NCH',
}

## Schedule Scraping

In [5]:
def get_schedule_html(year: str, month: str,):
    games = requests.get(f"https://www.basketball-reference.com/leagues/NBA_{year}_games-{month}.html#schedule")
    soup = BeautifulSoup(games.content, "html.parser")
    if soup.find('h1').text == 'Page Not Found (404 error)':
        return False
    else:
        return soup

In [6]:
def get_schedule_table(soup,):
    df = pd.read_html(str(soup.find_all('table')))[0].drop(['Unnamed: 6',], axis=1)
    return df

In [7]:
def process_schedule(df: pd.DataFrame):
    df = df.loc[df['Date'] != 'Playoffs'].copy()
    df['DateTime'] = pd.to_datetime(df['Date'] + ' ' + df['Start (ET)'] + 'm')
    df['DateStr'] = [dt.datetime.strftime(i, "%Y%m%d%H%M") for i in df['DateTime']]
    df = df.drop(['Date','Start (ET)','Notes'], axis=1)
    df.rename(columns={'Visitor/Neutral':'Visitor', 'PTS': 'Visitor PTS', 'Home/Neutral':'Home','PTS.1':'Home PTS', 'Unnamed: 7':'OT', 'Attend.':'Attendance'}, inplace=True)
    df['Visitor_short'] = [team_abbs[name] for name in df['Visitor']]
    df['Home_short'] = [team_abbs[name] for name in df['Home']]
    df['game_id'] = df['DateStr'] + df['Visitor_short'] + df['Home_short']
    df.set_index('DateTime', inplace=True)
    df['year'] = df.index.year
    df['month'] = df.index.month
    return df

In [ ]:
soup = get_schedule_html('2001','april')
df = get_schedule_table(soup)
df = process_schedule(df)

In [8]:
MONTHS = ['october','november','december','january','february','march','april','may','june','july','august','september']
YEARS = [str(i) for i in range(2001, dt.date.today().year + 1)]

In [268]:
df_list = []
request_count = 0
start = time.time()
for year in YEARS:
    for month in MONTHS[:]:
        lag = np.random.randint(4,6)
        print(f'Cycle lag time: {lag}')
        time.sleep(lag)
        print(f'Processing {month}-{year} request!')
        try:
            soup = get_schedule_html(year, month)
        except Exception as e:
            print(f'Could not process {month}-{year} request! {e}')
            continue
        if not soup:
            continue
        request_count += 1
        try:
            df = get_schedule_table(soup)
            df = process_schedule(df)
            df_list.append(df)
            print(f'Finished {month} request!')
        except:
            print(f'Error while processing {month}-{year}')
            continue
end = time.time()
print(f'Total time taken: {round(end-start)}s')
print(f'Total requests count: {request_count}')
print(f'Average Requests per Second: {round((end-start)/request_count)}')
full_df = pd.concat(df_list, axis=0)

Cycle lag time: 4
Processing june-2001 request!
Finished june request!
Cycle lag time: 4
Processing july-2001 request!
Cycle lag time: 5
Processing august-2001 request!
Cycle lag time: 5
Processing september-2001 request!
Cycle lag time: 5
Processing june-2002 request!
Finished june request!
Cycle lag time: 4
Processing july-2002 request!
Cycle lag time: 4
Processing august-2002 request!
Cycle lag time: 4
Processing september-2002 request!
Cycle lag time: 4
Processing june-2003 request!
Finished june request!
Cycle lag time: 4
Processing july-2003 request!
Cycle lag time: 5
Processing august-2003 request!
Cycle lag time: 4
Processing september-2003 request!
Cycle lag time: 5
Processing june-2004 request!
Finished june request!
Cycle lag time: 4
Processing july-2004 request!
Cycle lag time: 4
Processing august-2004 request!
Cycle lag time: 4
Processing september-2004 request!
Cycle lag time: 4
Processing june-2005 request!
Finished june request!
Cycle lag time: 5
Processing july-2005 re

In [270]:
if os.path.isfile('data/games_played.csv'):
    read_df = pd.read_csv('data/games_played.csv', index_col=0)
    final_df = pd.concat([read_df, full_df], axis=0).reset_index().drop_duplicates(subset='game_id')
    final_df.to_csv('data/games_played.csv')
else:
    full_df.to_csv('data/games_played.csv')

In [19]:
df_final = pd.read_csv('data/games_played.csv', index_col=0, parse_dates=['DateTime'], dtype={'DateStr':'str'}).sort_values('DateTime')

In [22]:
df_list = []
for i, x in enumerate(df_final['game_id']):
    lag = np.random.randint(4,6)
    print(f'Cycle lag time: {lag}')
    time.sleep(lag)
    team = df_final.loc[df_final['game_id'] == x, 'Home_short'][0]
    date = df_final.loc[df_final['game_id'] == x,].index[0]
    year = '{:04d}'.format(date.year)
    month = '{:02d}'.format(date.month)
    day = '{:02d}'.format(date.day)
    print(f'Processing {x} request!')
    try:
        test_soup = request_soup_for_game(year=year, month=month, day=day, team=team)
        print(f'Successfully processed {x} request!')
    except Exception as e:
        print(f'Request failed: {e}')
    try:
        shot_area = get_shot_area(test_soup)
        game_meta = get_game_meta(test_soup)
        df = create_df(shot_area, game_meta)
        df['game_id'] = x
        df_list.append(df)
        print(f'Successfully processed {x} shots!')

    except Exception as e:
        print(f'Could not get and process shots for {x}: {e}')
pbp_all = pd.concat(df_list, axis=0)

Cycle lag time: 4
Processing 200010311930CHHATL request!
Successfully processed 200010311930CHHATL request!
Successfully processed 200010311930CHHATL shots!
Cycle lag time: 4
Processing 200010311930CLENJN request!
Successfully processed 200010311930CLENJN request!
Successfully processed 200010311930CLENJN shots!
Cycle lag time: 5
Processing 200010311930WASORL request!
Successfully processed 200010311930WASORL request!
Successfully processed 200010311930WASORL shots!
Cycle lag time: 5
Processing 200010312000MILDAL request!
Successfully processed 200010312000MILDAL request!
Successfully processed 200010312000MILDAL shots!
Cycle lag time: 5
Processing 200010312000PHINYK request!
Successfully processed 200010312000PHINYK request!
Successfully processed 200010312000PHINYK shots!
Cycle lag time: 4
Processing 200010312000DETTOR request!
Successfully processed 200010312000DETTOR request!
Successfully processed 200010312000DETTOR shots!
Cycle lag time: 4
Processing 200010312030SACCHI request!
S

In [24]:
pbp_all.to_parquet('data\play_by_play.parquet')